In [1]:
import pandas as pd
import networkx as nx
import numpy as np
import folium

## Here

In [2]:
df = pd.read_csv('data/processed/Vacancy.csv', index_col=0, parse_dates = [2,3,4])

df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 366020 entries, 0 to 366019
Data columns (total 11 columns):
 #   Column               Non-Null Count   Dtype         
---  ------               --------------   -----         
 0   car                  366020 non-null  object        
 1   park_time            366020 non-null  datetime64[ns]
 2   reservation_time     366020 non-null  datetime64[ns]
 3   start_time           366020 non-null  datetime64[ns]
 4   time_to_reservation  366020 non-null  float64       
 5   time_to_start        366020 non-null  float64       
 6   park_location_lat    366020 non-null  float64       
 7   park_location_long   366020 non-null  float64       
 8   park_zone            366020 non-null  int64         
 9   park_battery         366020 non-null  int64         
 10  moved                366020 non-null  float64       
dtypes: datetime64[ns](3), float64(5), int64(2), object(1)
memory usage: 33.5+ MB


In [3]:
def haversine_alt(df, car1, car2):
    dfc1 = df[df.car == car1]
    dfc2 = df[df.car == car2]

    point1 = dfc1[['park_location_lat','park_location_long']].values[0]
    point2 = dfc2[['park_location_lat','park_location_long']].values[0]
    #return point1

    # convert decimal degrees to radians
    lat1, lon1 = map(np.radians, point1)
    lat2, lon2 = map(np.radians, point2)

    # Deltas
    delta_lon = lon2 - lon1 
    delta_lat = lat2 - lat1 
    
    # haversine formula 
    a = np.sin(delta_lat/2)**2 + np.cos(lat1) * np.cos(lat2) * np.sin(delta_lon/2)**2
    c = 2 * np.arcsin(np.sqrt(a)) 
    r = 6371000 # Radius of earth in m
    return c * r

In [4]:
def make_graph(df, timestamp, max_dist):
    def _edge_weight(x, max_dist):
        return max((max_dist-x)/max_dist,0)
    sub_df = df[(df.park_time < timestamp) & (df.reservation_time > timestamp)]
    sub_df = sub_df.assign(movedTF = (sub_df.moved > 100).astype(int))
    A = pd.DataFrame(data = [[_edge_weight(haversine_alt(sub_df, car1, car2), max_dist) for car1 in sub_df.car] for car2 in sub_df.car], index = sub_df.car, columns=sub_df.car)
    G = nx.from_pandas_adjacency(A)
    nx.set_node_attributes(G, sub_df.set_index('car').to_dict('index'))
    return G

In [5]:
timestamp = np.datetime64('2018-01-25T08:30:30')
sub_df = df[(df.park_time < timestamp) & (df.reservation_time > timestamp)]
G = make_graph(sub_df, timestamp, 1500)

In [6]:
node_attr = pd.DataFrame.from_dict(dict(G.nodes(data=True)), orient='index')
locations = {i: (r['park_location_lat'],r['park_location_long']) for i, r in node_attr.iterrows()}

A_flatten = pd.melt(nx.to_pandas_adjacency(G), ignore_index=False,var_name='car2', value_name='Weight').rename_axis("car1").reset_index()
A_flatten = A_flatten[A_flatten.Weight > 0]
A_flatten['car1'] = A_flatten['car1'].map(locations)
A_flatten['car2'] = A_flatten['car2'].map(locations)
A_flatten

car1                    car2    Weight
0      (55.783388, 12.517983)  (55.783388, 12.517983)  1.000000
40     (55.782498, 12.519595)  (55.783388, 12.517983)  0.905829
45     (55.779343, 12.519487)  (55.783388, 12.517983)  0.693660
54     (55.782374, 12.519525)  (55.783388, 12.517983)  0.901096
59     (55.769989, 12.516403)  (55.783388, 12.517983)  0.004551
...                       ...                     ...       ...
84310    (55.59233, 12.67601)  (55.585996, 12.658314)  0.122482
84388  (55.585996, 12.658314)  (55.585996, 12.658314)  1.000000
84575  (55.731345, 12.445186)  (55.733271, 12.444918)  0.856788
84591  (55.732392, 12.440973)  (55.733271, 12.444918)  0.822915
84680  (55.733271, 12.444918)  (55.733271, 12.444918)  1.000000

[4837 rows x 3 columns]

In [10]:
# Function to add a point to the map
def plot_cars(map, latitude, longitude, col = 4, tooltip = None):
    for lat, lon, c, tt in zip(latitude, longitude, col, tooltip):
        folium.CircleMarker(location=[lat, lon],
                                tooltip = tt,
                                radius=1.5,
                                weight=4,
                                color = c).add_to(map)

# Function to add edges
def plot_edges(map, edge_df):
    for _, r in edge_df.iterrows():
        folium.PolyLine([r['car1'],r['car2']],
                    color='black',
                    weight=1,
                    opacity=r['Weight']).add_to(map)

# Initialize map
m = folium.Map(location=[55.69, 12.568337], zoom_start=12, prefer_canvas=True)

# Add points
plot_cars(m, node_attr['park_location_lat'], node_attr['park_location_long'], node_attr.replace({"movedTF": {0: 'Red', 1: 'Blue'}})['movedTF'],  node_attr.index)# + "<br>" + node_attr['park_battery'])

plot_edges(m, A_flatten)

# Show map
m

In [1]:
1+1

2